In [1]:
import pandas as pd
import numpy as np

In [2]:
import matplotlib.pyplot as plt

In [3]:
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.ensemble import RandomForestRegressor
from xgboost import XGBRegressor
from lightgbm import LGBMRegressor
from sklearn.metrics import mean_squared_error
from sklearn.ensemble import StackingRegressor
from sklearn.linear_model import Ridge
from catboost import CatBoostRegressor
import optuna

C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [4]:
from sklearn.linear_model import ElasticNet, HuberRegressor, Lasso, BayesianRidge
from sklearn.neural_network import MLPRegressor
from sklearn.inspection import permutation_importance
from sklearn.ensemble import GradientBoostingRegressor, BaggingRegressor
from sklearn.kernel_ridge import KernelRidge
from sklearn.svm import SVR
from pytorch_tabnet.tab_model import TabNetRegressor
from sklearn.base import BaseEstimator, RegressorMixin

In [5]:
#model training, base models
train_processed = pd.read_csv('train_processed.csv')
test_processed = pd.read_csv('test_processed.csv')

# define features and target variable
X = train_processed.drop(['SalePrice'], axis=1)
y = train_processed['SalePrice']  # log transformed
X_test = test_processed.copy()
test = pd.read_csv('test.csv')
test_ID = test['Id']  # save test IDs for submission

# split train and validation sets,这里需要分层划分,以避免famd出现问题
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, random_state=42)

In [6]:
# 默认参数基模型训练（使用降维后数据）
# Random Forest
rf = RandomForestRegressor(random_state=42)
rf.fit(X_train, y_train)
rf_pred = rf.predict(X_val)
rf_rmse = np.sqrt(mean_squared_error(y_val, rf_pred))
print(f"RandomForest RMSE (default): {rf_rmse:.5f}")

# XGBoost
xgb = XGBRegressor(random_state=42)
xgb.fit(X_train, y_train)
xgb_pred = xgb.predict(X_val)
xgb_rmse = np.sqrt(mean_squared_error(y_val, xgb_pred))
print(f"XGBoost RMSE (default): {xgb_rmse:.5f}")

# LightGBM
lgb = LGBMRegressor(random_state=42,verbose=-1)
lgb.fit(X_train, y_train)
lgb_pred = lgb.predict(X_val)
lgb_rmse = np.sqrt(mean_squared_error(y_val, lgb_pred))
print(f"LightGBM RMSE (default): {lgb_rmse:.5f}")

# CatBoost（降维后无需 categorical_features）
# define categorical features for CatBoost
categorical_features = ['MSZoning', 'Street', 'Alley', 'LotShape', 'LandContour', 'Utilities', 
                       'LotConfig', 'LandSlope', 'Neighborhood', 'Condition1', 'Condition2', 
                       'BldgType', 'HouseStyle', 'RoofStyle', 'RoofMatl', 'Exterior1st', 
                       'Exterior2nd', 'MasVnrType', 'Foundation', 'BsmtFinType1', 
                       'BsmtFinType2', 'Heating', 'CentralAir', 'Electrical', 'GarageType', 
                       'GarageFinish', 'PavedDrive', 'Fence', 'MiscFeature', 'SaleType', 
                       'SaleCondition', 'Season']
catboost = CatBoostRegressor(random_state=42, verbose=0, cat_features=categorical_features)
catboost.fit(X_train, y_train, eval_set=(X_val, y_val), early_stopping_rounds=50)
catboost_pred = catboost.predict(X_val)
catboost_rmse = np.sqrt(mean_squared_error(y_val, catboost_pred))
print(f"CatBoost RMSE (default): {catboost_rmse:.5f}")

# enet
enet = ElasticNet(random_state=42)
enet.fit(X_train, y_train)
enet_pred = enet.predict(X_val)
enet_rmse = np.sqrt(mean_squared_error(y_val, enet_pred))
print(f"ElasticNet RMSE (default): {enet_rmse:.5f}")

# HuberRegressor
huber = HuberRegressor()
huber.fit(X_train, y_train)
huber_pred = huber.predict(X_val)
huber_rmse = np.sqrt(mean_squared_error(y_val, huber_pred))
print(f"HuberRegressor RMSE (default): {huber_rmse:.5f}")

# MLPRegressor
mlp = MLPRegressor(random_state=42, max_iter=1000)
mlp.fit(X_train, y_train)
mlp_pred = mlp.predict(X_val)
mlp_rmse = np.sqrt(mean_squared_error(y_val, mlp_pred))
print(f"MLPRegressor RMSE (default): {mlp_rmse:.5f}")

# KernelRidge
kr = KernelRidge()
kr.fit(X_train, y_train)
kr_pred = kr.predict(X_val)
kr_rmse = np.sqrt(mean_squared_error(y_val, kr_pred))
print(f"KernelRidge RMSE (default): {kr_rmse:.5f}")

# SVR
svr = SVR()
svr.fit(X_train, y_train)
svr_pred = svr.predict(X_val)
svr_rmse = np.sqrt(mean_squared_error(y_val, svr_pred))
print(f"SVR RMSE (default): {svr_rmse:.5f}")

# Ridge
ridge = Ridge()
ridge.fit(X_train, y_train)
ridge_pred = ridge.predict(X_val)
ridge_rmse = np.sqrt(mean_squared_error(y_val, ridge_pred))
print(f"Ridge RMSE (default): {ridge_rmse:.5f}")

# Lasso
lasso = Lasso()
lasso.fit(X_train, y_train)
lasso_pred = lasso.predict(X_val)
lasso_rmse = np.sqrt(mean_squared_error(y_val, lasso_pred))
print(f"Lasso RMSE (default): {lasso_rmse:.5f}")

# GBR
gbr = GradientBoostingRegressor()
gbr.fit(X_train, y_train)
gbr_pred = gbr.predict(X_val)
gbr_rmse = np.sqrt(mean_squared_error(y_val, gbr_pred))
print(f"GBR RMSE (default): {gbr_rmse:.5f}")

# bagging
bagging = BaggingRegressor()
bagging.fit(X_train, y_train)
bagging_pred = bagging.predict(X_val)
bagging_rmse = np.sqrt(mean_squared_error(y_val, bagging_pred))
print(f"Bagging RMSE (default): {bagging_rmse:.5f}")

# TabNet
tabnet = TabNetRegressor()
X_train_np = X_train.values
y_train_np = y_train.values.reshape(-1,1)
X_val_np = X_val.values
tabnet.fit(X_train_np, y_train_np)
tabnet_pred = tabnet.predict(X_val_np)
tabnet_rmse = np.sqrt(mean_squared_error(y_val, tabnet_pred))
print(f"TabNet RMSE (default): {tabnet_rmse:.5f}")


# BayesianRidge
bayesian_ridge = BayesianRidge()
bayesian_ridge.fit(X_train, y_train)
bayesian_ridge_pred = bayesian_ridge.predict(X_val)
bayesian_ridge_rmse = np.sqrt(mean_squared_error(y_val, bayesian_ridge_pred))
print(f"BayesianRidge RMSE (default): {bayesian_ridge_rmse:.5f}")


RandomForest RMSE (default): 0.14926
XGBoost RMSE (default): 0.14401
LightGBM RMSE (default): 0.14075
CatBoost RMSE (default): 0.12099
ElasticNet RMSE (default): 0.39872
HuberRegressor RMSE (default): 0.47456


C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\sklearn\linear_model\_huber.py:343: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. OF ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
  self.n_iter_ = _check_optimize_result("lbfgs", opt_res, self.max_iter)


MLPRegressor RMSE (default): 0.39593
KernelRidge RMSE (default): 0.19165
SVR RMSE (default): 0.12493
Ridge RMSE (default): 0.12647
Lasso RMSE (default): 0.39872
GBR RMSE (default): 0.12996
Bagging RMSE (default): 0.14829


C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\pytorch_tabnet\abstract_model.py:82: UserWarning: Device used : cpu
  warnings.warn(f"Device used : {self.device}")
C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\pytorch_tabnet\abstract_model.py:687: UserWarning: No early stopping will be performed, last training weights will be used.
  warnings.warn(wrn_msg)


epoch 0  | loss: 135.58453|  0:00:00s
epoch 1  | loss: 126.61742|  0:00:00s
epoch 2  | loss: 118.36626|  0:00:00s
epoch 3  | loss: 110.15644|  0:00:00s
epoch 4  | loss: 102.71006|  0:00:00s
epoch 5  | loss: 95.35297|  0:00:00s
epoch 6  | loss: 88.73606|  0:00:00s
epoch 7  | loss: 81.94154|  0:00:00s
epoch 8  | loss: 72.13223|  0:00:00s
epoch 9  | loss: 64.87029|  0:00:00s
epoch 10 | loss: 59.12515|  0:00:00s
epoch 11 | loss: 50.73232|  0:00:00s
epoch 12 | loss: 43.19045|  0:00:00s
epoch 13 | loss: 37.31705|  0:00:00s
epoch 14 | loss: 30.85492|  0:00:00s
epoch 15 | loss: 24.46004|  0:00:00s
epoch 16 | loss: 20.09502|  0:00:00s
epoch 17 | loss: 15.65094|  0:00:01s
epoch 18 | loss: 11.24824|  0:00:01s
epoch 19 | loss: 8.46251 |  0:00:01s
epoch 20 | loss: 5.59406 |  0:00:01s
epoch 21 | loss: 4.66188 |  0:00:01s
epoch 22 | loss: 4.18116 |  0:00:01s
epoch 23 | loss: 4.65246 |  0:00:01s
epoch 24 | loss: 5.34922 |  0:00:01s
epoch 25 | loss: 5.47355 |  0:00:01s
epoch 26 | loss: 5.46906 |  0:00:

In [ ]:
n_trials = 500
n_trials_fast = 2000
n_trials_slow = 300
n_trials_verySLOW = 100

In [8]:
# RandomForest optuna 调优
def rf_objective(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 100, 1000),
        'max_depth': trial.suggest_int('max_depth', 3, 20),
        'min_samples_split': trial.suggest_int('min_samples_split', 2, 10),
        'min_samples_leaf': trial.suggest_int('min_samples_leaf', 1, 4),
        'random_state': 42
    }
    model = RandomForestRegressor(**params)
    model.fit(X_train, y_train)
    pred = model.predict(X_val)
    return np.sqrt(mean_squared_error(y_val, pred))

rf_study = optuna.create_study(direction='minimize')
rf_study.optimize(rf_objective, n_trials=50)  # RF 调优较慢，减少 trials
rf_best_params = rf_study.best_params
print("Best RandomForest params (Optuna):", rf_best_params)

# 重训练 Random Forest
rf_best = RandomForestRegressor(**rf_best_params, random_state=42)
rf_best.fit(X_train, y_train)
rf_best_pred = rf_best.predict(X_val)
rf_best_rmse = np.sqrt(mean_squared_error(y_val, rf_best_pred))
print(f"Optuna tuned RandomForest RMSE (reduced): {rf_best_rmse:.5f}")

[I 2025-08-17 13:55:55,686] A new study created in memory with name: no-name-3bb17441-ce4a-433f-bb12-301962a9d4ea
[I 2025-08-17 13:56:09,209] Trial 0 finished with value: 0.14893528645314605 and parameters: {'n_estimators': 846, 'max_depth': 13, 'min_samples_split': 9, 'min_samples_leaf': 3}. Best is trial 0 with value: 0.14893528645314605.
[I 2025-08-17 13:56:14,684] Trial 1 finished with value: 0.1491181422699895 and parameters: {'n_estimators': 353, 'max_depth': 10, 'min_samples_split': 10, 'min_samples_leaf': 2}. Best is trial 0 with value: 0.14893528645314605.
[I 2025-08-17 13:56:26,831] Trial 2 finished with value: 0.1497437152381849 and parameters: {'n_estimators': 783, 'max_depth': 14, 'min_samples_split': 2, 'min_samples_leaf': 4}. Best is trial 0 with value: 0.14893528645314605.
[I 2025-08-17 13:56:35,290] Trial 3 finished with value: 0.1561551611268414 and parameters: {'n_estimators': 773, 'max_depth': 6, 'min_samples_split': 4, 'min_samples_leaf': 4}. Best is trial 0 with v

Best RandomForest params (Optuna): {'n_estimators': 634, 'max_depth': 17, 'min_samples_split': 3, 'min_samples_leaf': 1}
Optuna tuned RandomForest RMSE (reduced): 0.14611


In [9]:
# 使用 Optuna 调优（每个模型单独定义 objective）
# XGBoost Optuna 调优
def xgb_objective(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 100, 1000),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.1),
        'max_depth': trial.suggest_int('max_depth', 3, 7),
        'subsample': trial.suggest_float('subsample', 0.7, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.7, 1.0),
        'min_child_weight': trial.suggest_int('min_child_weight', 1, 5),
        'random_state': 42
    }
    model = XGBRegressor(**params)
    model.fit(X_train, y_train)
    pred = model.predict(X_val)
    return np.sqrt(mean_squared_error(y_val, pred))

xgb_study = optuna.create_study(direction='minimize')
xgb_study.optimize(xgb_objective, n_trials=n_trials)
xgb_best_params = xgb_study.best_params
print("Best XGBoost params (Optuna):", xgb_best_params)

# 重训练 XGBoost
xgb_best = XGBRegressor(**xgb_best_params, random_state=42)
xgb_best.fit(X_train, y_train)
xgb_best_pred = xgb_best.predict(X_val)
xgb_best_rmse = np.sqrt(mean_squared_error(y_val, xgb_best_pred))
print(f"Optuna tuned XGBoost RMSE (reduced): {xgb_best_rmse:.5f}")

[I 2025-08-17 14:04:42,413] A new study created in memory with name: no-name-f6bc5570-1056-4787-a759-dfa89927e34c
[I 2025-08-17 14:04:43,558] Trial 0 finished with value: 0.1349737097698185 and parameters: {'n_estimators': 621, 'learning_rate': 0.046288569393954954, 'max_depth': 7, 'subsample': 0.9272320249404369, 'colsample_bytree': 0.9822661503783987, 'min_child_weight': 3}. Best is trial 0 with value: 0.1349737097698185.
[I 2025-08-17 14:04:44,395] Trial 1 finished with value: 0.13312569193503435 and parameters: {'n_estimators': 585, 'learning_rate': 0.039074972328478286, 'max_depth': 6, 'subsample': 0.956428210449832, 'colsample_bytree': 0.9459690469951276, 'min_child_weight': 2}. Best is trial 1 with value: 0.13312569193503435.
[I 2025-08-17 14:04:45,090] Trial 2 finished with value: 0.12300729217740373 and parameters: {'n_estimators': 944, 'learning_rate': 0.015641567707807058, 'max_depth': 3, 'subsample': 0.8943833750045844, 'colsample_bytree': 0.8284706668835706, 'min_child_wei

Best XGBoost params (Optuna): {'n_estimators': 988, 'learning_rate': 0.019794274040249325, 'max_depth': 3, 'subsample': 0.7189765754097851, 'colsample_bytree': 0.710355096448193, 'min_child_weight': 2}
Optuna tuned XGBoost RMSE (reduced): 0.11913


In [10]:
# LightGBM Optuna 调优
def lgb_objective(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 100, 1000),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.1),
        'max_depth': trial.suggest_int('max_depth', 3, 7),
        'num_leaves': trial.suggest_int('num_leaves', 15, 63),
        'subsample': trial.suggest_float('subsample', 0.7, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.7, 1.0),
        'random_state': 42
    }
    model = LGBMRegressor(**params)
    model.fit(X_train, y_train)
    pred = model.predict(X_val)
    return np.sqrt(mean_squared_error(y_val, pred))

lgb_study = optuna.create_study(direction='minimize')
lgb_study.optimize(lgb_objective, n_trials=n_trials)
lgb_best_params = lgb_study.best_params
print("Best LightGBM params (Optuna):", lgb_best_params)

# 重训练 LightGBM
lgb_best = LGBMRegressor(**lgb_best_params, random_state=42,verbose=-1)
lgb_best.fit(X_train, y_train)
lgb_best_pred = lgb_best.predict(X_val)
lgb_best_rmse = np.sqrt(mean_squared_error(y_val, lgb_best_pred))
print(f"Optuna tuned LightGBM RMSE (reduced): {lgb_best_rmse:.5f}")

[I 2025-08-17 14:09:43,867] A new study created in memory with name: no-name-5f6fa6ed-b82f-4f73-9160-360d026c7a52
[I 2025-08-17 14:09:44,017] Trial 0 finished with value: 0.1358173270949269 and parameters: {'n_estimators': 307, 'learning_rate': 0.06585790912933305, 'max_depth': 6, 'num_leaves': 35, 'subsample': 0.8315599488207487, 'colsample_bytree': 0.8891784470493316}. Best is trial 0 with value: 0.1358173270949269.
[I 2025-08-17 14:09:44,342] Trial 1 finished with value: 0.1371941518160453 and parameters: {'n_estimators': 650, 'learning_rate': 0.03145844471764888, 'max_depth': 7, 'num_leaves': 43, 'subsample': 0.80612289760603, 'colsample_bytree': 0.8970838618013401}. Best is trial 0 with value: 0.1358173270949269.
[I 2025-08-17 14:09:44,564] Trial 2 finished with value: 0.13501272791092808 and parameters: {'n_estimators': 331, 'learning_rate': 0.0201826511398743, 'max_depth': 7, 'num_leaves': 45, 'subsample': 0.813389752318502, 'colsample_bytree': 0.892876626279776}. Best is trial 

Best LightGBM params (Optuna): {'n_estimators': 354, 'learning_rate': 0.04776311085216704, 'max_depth': 3, 'num_leaves': 42, 'subsample': 0.9193871451479886, 'colsample_bytree': 0.7650869103903398}
Optuna tuned LightGBM RMSE (reduced): 0.12436


In [11]:
# CatBoost Optuna 调优
def catboost_objective(trial):
    params = {
        'iterations': 500,  # 初始小值，之后可增大
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.05),
        'depth': trial.suggest_int('depth', 4, 10),
        'l2_leaf_reg': trial.suggest_int('l2_leaf_reg', 1, 7),
        'bagging_temperature': trial.suggest_float('bagging_temperature', 0, 1),
        'border_count': trial.suggest_int('border_count', 32, 128),
        'random_state': 42,
        'verbose': 0
    }
    model = CatBoostRegressor(**params)
    model.fit(X_train, y_train, eval_set=(X_val, y_val), early_stopping_rounds=50)
    pred = model.predict(X_val)
    return np.sqrt(mean_squared_error(y_val, pred))

catboost_study = optuna.create_study(direction='minimize')
catboost_study.optimize(catboost_objective, n_trials=n_trials)
catboost_best_params = catboost_study.best_params
catboost_best_params['iterations'] = 5000  # 增大 iterations 以利用最佳参数
print("Best CatBoost params (Optuna):", catboost_best_params)

# 重训练 CatBoost
catboost_best = CatBoostRegressor(**catboost_best_params, random_state=42, verbose=100)
catboost_best.fit(X_train, y_train, eval_set=(X_val, y_val), early_stopping_rounds=200)
catboost_best_pred = catboost_best.predict(X_val)
catboost_best_rmse = np.sqrt(mean_squared_error(y_val, catboost_best_pred))
print(f"Optuna tuned CatBoost RMSE (reduced): {catboost_best_rmse:.5f}")

[I 2025-08-17 14:11:25,421] A new study created in memory with name: no-name-d978143c-4a0a-40ae-a8e9-3a7c551f201e
[I 2025-08-17 14:11:25,944] Trial 0 finished with value: 0.1230552931963508 and parameters: {'learning_rate': 0.018302708555470924, 'depth': 4, 'l2_leaf_reg': 4, 'bagging_temperature': 0.1583618424531874, 'border_count': 63}. Best is trial 0 with value: 0.1230552931963508.
[I 2025-08-17 14:11:28,550] Trial 1 finished with value: 0.12758830995417908 and parameters: {'learning_rate': 0.03360080017187816, 'depth': 9, 'l2_leaf_reg': 2, 'bagging_temperature': 0.9023532415811185, 'border_count': 87}. Best is trial 0 with value: 0.1230552931963508.
[I 2025-08-17 14:11:33,235] Trial 2 finished with value: 0.13889120381284617 and parameters: {'learning_rate': 0.011140678037650611, 'depth': 10, 'l2_leaf_reg': 4, 'bagging_temperature': 0.2991059698930061, 'border_count': 67}. Best is trial 0 with value: 0.1230552931963508.
[I 2025-08-17 14:11:34,157] Trial 3 finished with value: 0.119

Best CatBoost params (Optuna): {'learning_rate': 0.047348295109695564, 'depth': 4, 'l2_leaf_reg': 7, 'bagging_temperature': 0.9179362159349008, 'border_count': 69, 'iterations': 5000}
0:	learn: 0.3844658	test: 0.3877756	best: 0.3877756 (0)	total: 1.29ms	remaining: 6.43s
100:	learn: 0.1197579	test: 0.1341631	best: 0.1341631 (100)	total: 106ms	remaining: 5.13s
200:	learn: 0.0989267	test: 0.1201247	best: 0.1201247 (200)	total: 192ms	remaining: 4.59s
300:	learn: 0.0872445	test: 0.1158456	best: 0.1158456 (300)	total: 289ms	remaining: 4.51s
400:	learn: 0.0803419	test: 0.1145097	best: 0.1144763 (393)	total: 369ms	remaining: 4.23s
500:	learn: 0.0749267	test: 0.1135765	best: 0.1134984 (488)	total: 452ms	remaining: 4.06s
600:	learn: 0.0702428	test: 0.1131120	best: 0.1131069 (599)	total: 539ms	remaining: 3.95s
700:	learn: 0.0654238	test: 0.1128547	best: 0.1128278 (698)	total: 623ms	remaining: 3.82s
800:	learn: 0.0617660	test: 0.1132055	best: 0.1128278 (698)	total: 705ms	remaining: 3.69s
Stopped b

In [12]:
#  ElasticNet 调优
def enet_objective(trial):
    params = {
        'alpha': trial.suggest_float('alpha', 0.0001, 1.0, log=True),
        'l1_ratio': trial.suggest_float('l1_ratio', 0.0, 1.0),
        'random_state': 42
    }
    model = ElasticNet(**params)
    model.fit(X_train, y_train)
    pred = model.predict(X_val)
    return np.sqrt(mean_squared_error(y_val, pred))

enet_study = optuna.create_study(direction='minimize')
enet_study.optimize(enet_objective, n_trials=n_trials)
enet_best_params = enet_study.best_params
print("Best ElasticNet params (Optuna):", enet_best_params)

# 重训练 ElasticNet
enet_best = ElasticNet(**enet_best_params, random_state=42)
enet_best.fit(X_train, y_train)
enet_best_pred = enet_best.predict(X_val)
enet_best_rmse = np.sqrt(mean_squared_error(y_val, enet_best_pred))
print(f"Optuna tuned ElasticNet RMSE: {enet_best_rmse:.5f}")

[I 2025-08-17 14:17:09,775] A new study created in memory with name: no-name-e89d6177-42dc-4a60-9332-f12be425ae78
[I 2025-08-17 14:17:09,801] Trial 0 finished with value: 0.12890545259898056 and parameters: {'alpha': 0.0073029674005703595, 'l1_ratio': 0.3589288827349081}. Best is trial 0 with value: 0.12890545259898056.
[I 2025-08-17 14:17:09,811] Trial 1 finished with value: 0.17990599314843778 and parameters: {'alpha': 0.07354117713007033, 'l1_ratio': 0.8404284712526936}. Best is trial 0 with value: 0.12890545259898056.
[I 2025-08-17 14:17:09,850] Trial 2 finished with value: 0.22811076086779686 and parameters: {'alpha': 0.6651165863598331, 'l1_ratio': 0.17868108038894936}. Best is trial 0 with value: 0.12890545259898056.
[I 2025-08-17 14:17:09,865] Trial 3 finished with value: 0.13822410118093528 and parameters: {'alpha': 0.03530125968548853, 'l1_ratio': 0.4523750049099472}. Best is trial 0 with value: 0.12890545259898056.
[I 2025-08-17 14:17:09,884] Trial 4 finished with value: 0.1

Best ElasticNet params (Optuna): {'alpha': 0.0001003776370975647, 'l1_ratio': 0.17342638714417052}
Optuna tuned ElasticNet RMSE: 0.12617


C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\sklearn\linear_model\_coordinate_descent.py:695: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 4.689e+00, tolerance: 1.819e-02
  model = cd_fast.enet_coordinate_descent(


In [13]:
# Huber 调优
def objective_huber(trial):
    params = {
        'alpha': trial.suggest_float('alpha', 1e-4, 0.1, log=True),
        'epsilon': trial.suggest_float('epsilon', 1.0, 2.0),
        'max_iter': trial.suggest_int('max_iter', 2000, 5000)
    }
    model = HuberRegressor(**params)
    model.fit(X_train, y_train)
    pred = model.predict(X_val)
    rmse = np.sqrt(mean_squared_error(y_val, pred))
    return rmse

study_huber = optuna.create_study(direction='minimize')
study_huber.optimize(objective_huber, n_trials=n_trials)
huber_best_params = study_huber.best_params
print("best Huber params:", study_huber.best_params)
print("best Huber RMSE:", study_huber.best_value)

# retrain
huber_best = HuberRegressor(**study_huber.best_params)
huber_best.fit(X_train, y_train)
huber_best_pred = huber_best.predict(X_val)
huber_best_rmse = np.sqrt(mean_squared_error(y_val, huber_best_pred))
print(f"Tuned Huber RMSE: {huber_best_rmse:.5f}")


[I 2025-08-17 14:17:39,357] A new study created in memory with name: no-name-a0590026-6e24-48d9-89b2-c46671118e08
[I 2025-08-17 14:17:41,679] Trial 0 finished with value: 0.12708972661000012 and parameters: {'alpha': 0.008592085001656733, 'epsilon': 1.1638321595371197, 'max_iter': 4226}. Best is trial 0 with value: 0.12708972661000012.
[I 2025-08-17 14:17:43,689] Trial 1 finished with value: 0.12670504824957415 and parameters: {'alpha': 0.0005344941972691237, 'epsilon': 1.2673998024820374, 'max_iter': 3630}. Best is trial 1 with value: 0.12670504824957415.
C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\sklearn\linear_model\_huber.py:343: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. OF ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
  self.n_iter_ = _check_optimize_result("lbfgs", opt_res, self.max_iter)
[I 2025-08-17 14:17:45,6

best Huber params: {'alpha': 0.07858893948127713, 'epsilon': 1.965637104417994, 'max_iter': 2054}
best Huber RMSE: 0.12390182950494899
Tuned Huber RMSE: 0.12390


C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\sklearn\linear_model\_huber.py:343: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. OF ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
  self.n_iter_ = _check_optimize_result("lbfgs", opt_res, self.max_iter)


In [ ]:
# MLP 调优
def objective_mlp(trial):
    params = {
        'hidden_layer_sizes': trial.suggest_categorical('hidden_layer_sizes', [(50,100,50), (50,100,200,100,50), 
                                                                               (50,100,200,300,200,100,50), (100, 100),
                                                                               (100,200,100),(100,200,300,200,100),
                                                                               (100,200,300,400,300,200,100)]),
        'alpha': trial.suggest_float('alpha', 1e-5, 1e-2, log=True),
        'learning_rate_init': trial.suggest_float('learning_rate_init', 1e-4, 1e-2, log=True),
        'max_iter': trial.suggest_int('max_iter', 200, 1000)
    }
    model = MLPRegressor(**params, random_state=42)
    model.fit(X_train, y_train)
    pred = model.predict(X_val)
    rmse = np.sqrt(mean_squared_error(y_val, pred))
    return rmse

study_mlp = optuna.create_study(direction='minimize')
study_mlp.optimize(objective_mlp, n_trials=n_trials)
mlp_best_params = study_mlp.best_params
mlp_best_params['max_iter'] = 5000  # increase iterations 
print("Best MLP params:", study_mlp.best_params)
print("Best MLP RMSE:", study_mlp.best_value)

# retrain
mlp_best = MLPRegressor(**mlp_best_params, random_state=42)
mlp_best.fit(X_train, y_train)
mlp_best_pred = mlp_best.predict(X_val)
mlp_best_rmse = np.sqrt(mean_squared_error(y_val, mlp_best_pred))
print(f"Tuned MLP RMSE: {mlp_best_rmse:.5f}")


[I 2025-08-17 14:32:59,391] A new study created in memory with name: no-name-4d74ee4f-58e7-48b3-a613-df16b1b7b68b
C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\optuna\distributions.py:518: UserWarning: Choices for a categorical distribution should be a tuple of None, bool, int, float and str for persistent storage but contains (50, 100, 50) which is of type tuple.
  warnings.warn(message)
C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\optuna\distributions.py:518: UserWarning: Choices for a categorical distribution should be a tuple of None, bool, int, float and str for persistent storage but contains (50, 100, 200, 100, 50) which is of type tuple.
  warnings.warn(message)
C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\optuna\distributions.py:518: UserWarning: Choices for a categorical distribution should be a tuple of None, bool, int, float and str for persistent storage but contains (50, 100, 200, 300, 200, 100, 50) which is of type tuple.

Best MLP params: {'hidden_layer_sizes': (100, 200, 300, 400, 300, 200, 100), 'alpha': 0.008242160412638026, 'learning_rate_init': 0.009087072551608025, 'max_iter': 677}
Best MLP RMSE: 0.15270290898143354
Tuned MLP RMSE: 0.15270


In [21]:
# retrain
mlp_best_params['max_iter'] = 5000  # increase iterations
mlp_best = MLPRegressor(**mlp_best_params, random_state=42)
mlp_best.fit(X_train, y_train)
mlp_best_pred = mlp_best.predict(X_val)
mlp_best_rmse = np.sqrt(mean_squared_error(y_val, mlp_best_pred))
print(f"Tuned MLP RMSE: {mlp_best_rmse:.5f}")

Tuned MLP RMSE: 0.15270


In [15]:
#  KernelRidge 调优
def kr_objective(trial):
    kernel = trial.suggest_categorical('kernel', ['rbf', 'linear'])
    params = {
        'alpha': trial.suggest_float('alpha', 0.1, 10.0, log=True),
        'kernel': kernel
    }
    if kernel == 'rbf':
        params['gamma'] = trial.suggest_float('gamma', 0.001, 0.1, log=True)
    model = KernelRidge(**params)
    model.fit(X_train, y_train)
    pred = model.predict(X_val)
    return np.sqrt(mean_squared_error(y_val, pred))

kr_study = optuna.create_study(direction='minimize')
kr_study.optimize(kr_objective, n_trials=n_trials)
kr_best_params = kr_study.best_params
print("Best KernelRidge params (Optuna):", kr_best_params)

# 重训练 KernelRidge
kr_best = KernelRidge(**kr_best_params)
kr_best.fit(X_train, y_train)
kr_best_pred = kr_best.predict(X_val)
kr_best_rmse = np.sqrt(mean_squared_error(y_val, kr_best_pred))
print(f"Optuna tuned KernelRidge RMSE: {kr_best_rmse:.5f}")

[I 2025-08-17 16:10:13,852] A new study created in memory with name: no-name-4358b341-e81b-49d6-a7f6-5cc21efbf535
[I 2025-08-17 16:10:13,910] Trial 0 finished with value: 0.12342998847935333 and parameters: {'kernel': 'linear', 'alpha': 0.1366345937651236}. Best is trial 0 with value: 0.12342998847935333.
[I 2025-08-17 16:10:13,952] Trial 1 finished with value: 0.12629009827489518 and parameters: {'kernel': 'linear', 'alpha': 0.20946464623038505}. Best is trial 0 with value: 0.12342998847935333.
[I 2025-08-17 16:10:14,008] Trial 2 finished with value: 1.6689621588746675 and parameters: {'kernel': 'rbf', 'alpha': 0.9189191311622981, 'gamma': 0.009421111865142143}. Best is trial 0 with value: 0.12342998847935333.
[I 2025-08-17 16:10:14,047] Trial 3 finished with value: 0.12343339078572813 and parameters: {'kernel': 'linear', 'alpha': 0.13678022185523697}. Best is trial 0 with value: 0.12342998847935333.
[I 2025-08-17 16:10:14,100] Trial 4 finished with value: 0.24823377820960807 and para

Best KernelRidge params (Optuna): {'kernel': 'linear', 'alpha': 0.10000382071679537}
Optuna tuned KernelRidge RMSE: 0.12293


In [16]:
# SVR 调优
def svr_objective(trial):
    params = {
        'C': trial.suggest_float('C', 0.1, 100.0, log=True),
        'epsilon': trial.suggest_float('epsilon', 0.01, 0.5),
        'kernel': trial.suggest_categorical('kernel', ['rbf', 'linear'])
    }
    model = SVR(**params)
    model.fit(X_train, y_train)
    pred = model.predict(X_val)
    return np.sqrt(mean_squared_error(y_val, pred))

svr_study = optuna.create_study(direction='minimize')
svr_study.optimize(svr_objective, n_trials=n_trials)
svr_best_params = svr_study.best_params
print("Best SVR params (Optuna):", svr_best_params)

# 重训练 SVR
svr_best = SVR(**svr_best_params)
svr_best.fit(X_train, y_train)
svr_best_pred = svr_best.predict(X_val)
svr_best_rmse = np.sqrt(mean_squared_error(y_val, svr_best_pred))
print(f"Optuna tuned SVR RMSE: {svr_best_rmse:.5f}")

[I 2025-08-17 16:10:35,951] A new study created in memory with name: no-name-38ed6bb5-e740-4ebf-8bf6-4a93d9423a44
[I 2025-08-17 16:10:35,963] Trial 0 finished with value: 0.19409168751910907 and parameters: {'C': 7.54630475676355, 'epsilon': 0.4875252811227908, 'kernel': 'linear'}. Best is trial 0 with value: 0.19409168751910907.
[I 2025-08-17 16:10:35,973] Trial 1 finished with value: 0.19375683401648186 and parameters: {'C': 3.9042858791275092, 'epsilon': 0.4148685796386942, 'kernel': 'rbf'}. Best is trial 1 with value: 0.19375683401648186.
[I 2025-08-17 16:10:36,036] Trial 2 finished with value: 0.12231649758205751 and parameters: {'C': 2.1177716828788324, 'epsilon': 0.08908094729720573, 'kernel': 'rbf'}. Best is trial 2 with value: 0.12231649758205751.
[I 2025-08-17 16:10:39,488] Trial 3 finished with value: 0.14766655343070093 and parameters: {'C': 7.8355781102640405, 'epsilon': 0.25319542656361627, 'kernel': 'linear'}. Best is trial 2 with value: 0.12231649758205751.
[I 2025-08-1

Best SVR params (Optuna): {'C': 1.91076115049394, 'epsilon': 0.021649017891148287, 'kernel': 'rbf'}
Optuna tuned SVR RMSE: 0.11893


In [17]:
# Optuna optimization for Ridge
def objective_ridge(trial):
    alpha = trial.suggest_float('alpha', 0.1, 10.0, log=True)
    ridge = Ridge(alpha=alpha, random_state=42)
    ridge.fit(X_train, y_train)
    pred = ridge.predict(X_val)
    rmse = np.sqrt(mean_squared_error(y_val, pred))
    return rmse

# Optimize hyperparameters with Optuna
study_ridge = optuna.create_study(direction='minimize')
study_ridge.optimize(objective_ridge, n_trials=n_trials)
print("Best Ridge params:", study_ridge.best_params)
print("Best Ridge RMSE:", study_ridge.best_value)

# retrain
ridge_best = Ridge(**study_ridge.best_params, random_state=42)
ridge_best.fit(X_train, y_train)
ridge_best_pred = ridge_best.predict(X_val)
ridge_best_rmse = np.sqrt(mean_squared_error(y_val, ridge_best_pred))
print(f"Tuned Ridge RMSE: {ridge_best_rmse:.5f}")

[I 2025-08-17 16:16:08,771] A new study created in memory with name: no-name-6b7fc230-a405-47d9-9e3d-9b4a87f7aa9a
[I 2025-08-17 16:16:08,782] Trial 0 finished with value: 0.1263303305271608 and parameters: {'alpha': 0.536955528334113}. Best is trial 0 with value: 0.1263303305271608.
[I 2025-08-17 16:16:08,789] Trial 1 finished with value: 0.12642170503455927 and parameters: {'alpha': 0.8260566898012637}. Best is trial 0 with value: 0.1263303305271608.
[I 2025-08-17 16:16:08,797] Trial 2 finished with value: 0.12617480579148105 and parameters: {'alpha': 0.12240011646972151}. Best is trial 2 with value: 0.12617480579148105.
[I 2025-08-17 16:16:08,805] Trial 3 finished with value: 0.1271165775620117 and parameters: {'alpha': 4.314018751000626}. Best is trial 2 with value: 0.12617480579148105.
[I 2025-08-17 16:16:08,812] Trial 4 finished with value: 0.126995964687263 and parameters: {'alpha': 3.4769697169088576}. Best is trial 2 with value: 0.12617480579148105.
[I 2025-08-17 16:16:08,819] 

Best Ridge params: {'alpha': 0.10000473330039265}
Best Ridge RMSE: 0.1261635855204583
Tuned Ridge RMSE: 0.12616


In [18]:
# Optuna optimization for Lasso
def objective_lasso(trial):
    alpha = trial.suggest_float('alpha', 0.0001, 0.1, log=True)
    lasso = Lasso(alpha=alpha, random_state=42)
    lasso.fit(X_train, y_train)
    pred = lasso.predict(X_val)
    rmse = np.sqrt(mean_squared_error(y_val, pred))
    return rmse

# Optimize hyperparameters with Optuna
study_lasso = optuna.create_study(direction='minimize')
study_lasso.optimize(objective_lasso, n_trials=n_trials)
print("Best Lasso params:", study_lasso.best_params)
print("Best Lasso RMSE:", study_lasso.best_value)

# retrain
lasso_best = Lasso(**study_lasso.best_params, random_state=42)
lasso_best.fit(X_train, y_train)
lasso_best_pred = lasso_best.predict(X_val)
lasso_best_rmse = np.sqrt(mean_squared_error(y_val, lasso_best_pred))
print(f"Tuned Lasso RMSE: {lasso_best_rmse:.5f}")

[I 2025-08-17 16:16:14,227] A new study created in memory with name: no-name-b53575d2-e61a-4322-bc1e-42fcca6c9722
[I 2025-08-17 16:16:14,266] Trial 0 finished with value: 0.12762694801391816 and parameters: {'alpha': 0.0006527198871845362}. Best is trial 0 with value: 0.12762694801391816.
[I 2025-08-17 16:16:14,297] Trial 1 finished with value: 0.12766954578042974 and parameters: {'alpha': 0.00069664145780777}. Best is trial 0 with value: 0.12762694801391816.
[I 2025-08-17 16:16:14,317] Trial 2 finished with value: 0.13905317452194169 and parameters: {'alpha': 0.015816031099705995}. Best is trial 0 with value: 0.12762694801391816.
[I 2025-08-17 16:16:14,338] Trial 3 finished with value: 0.13830813386221802 and parameters: {'alpha': 0.015229912208978715}. Best is trial 0 with value: 0.12762694801391816.
[I 2025-08-17 16:16:14,345] Trial 4 finished with value: 0.19495224353261154 and parameters: {'alpha': 0.08479339745672594}. Best is trial 0 with value: 0.12762694801391816.
[I 2025-08-1

Best Lasso params: {'alpha': 0.0001000058995669444}
Best Lasso RMSE: 0.12638472958333277
Tuned Lasso RMSE: 0.12638


C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\sklearn\linear_model\_coordinate_descent.py:695: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 8.128e-01, tolerance: 1.819e-02
  model = cd_fast.enet_coordinate_descent(


In [22]:
# Optuna optimization for GradientBoosting
def objective_gbr(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 100, 1000),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.1, log=True),
        'max_depth': trial.suggest_int('max_depth', 3, 7),
        'min_samples_split': trial.suggest_int('min_samples_split', 2, 10),
        'min_samples_leaf': trial.suggest_int('min_samples_leaf', 1, 4),
        'subsample': trial.suggest_float('subsample', 0.7, 1.0)
    }
    gbr = GradientBoostingRegressor(**params, random_state=42)
    gbr.fit(X_train, y_train)
    pred = gbr.predict(X_val)
    rmse = np.sqrt(mean_squared_error(y_val, pred))
    return rmse

# Optimize hyperparameters with Optuna
study_gbr = optuna.create_study(direction='minimize')
study_gbr.optimize(objective_gbr, n_trials=n_trials)
print("Best GradientBoosting params:", study_gbr.best_params)
print("Best GradientBoosting RMSE:", study_gbr.best_value)

# retrain
gbr_best = GradientBoostingRegressor(**study_gbr.best_params, random_state=42)
gbr_best.fit(X_train, y_train)
gbr_best_pred = gbr_best.predict(X_val)
gbr_best_rmse = np.sqrt(mean_squared_error(y_val, gbr_best_pred))
print(f"Tuned GradientBoosting RMSE: {gbr_best_rmse:.5f}")

[I 2025-08-17 16:47:02,459] A new study created in memory with name: no-name-497d994e-ddf1-4488-afe8-a4ebcbd8cf69
[I 2025-08-17 16:47:15,250] Trial 0 finished with value: 0.13296730040686 and parameters: {'n_estimators': 847, 'learning_rate': 0.019584772954981174, 'max_depth': 6, 'min_samples_split': 9, 'min_samples_leaf': 4, 'subsample': 0.8712392872673951}. Best is trial 0 with value: 0.13296730040686.
[I 2025-08-17 16:47:19,872] Trial 1 finished with value: 0.13064949723067268 and parameters: {'n_estimators': 515, 'learning_rate': 0.09222301784486779, 'max_depth': 3, 'min_samples_split': 10, 'min_samples_leaf': 1, 'subsample': 0.9822480140359107}. Best is trial 1 with value: 0.13064949723067268.
[I 2025-08-17 16:47:24,748] Trial 2 finished with value: 0.13091164181894915 and parameters: {'n_estimators': 356, 'learning_rate': 0.04733986864157737, 'max_depth': 6, 'min_samples_split': 4, 'min_samples_leaf': 1, 'subsample': 0.7464906261029561}. Best is trial 1 with value: 0.130649497230

Best GradientBoosting params: {'n_estimators': 807, 'learning_rate': 0.03264158995949075, 'max_depth': 3, 'min_samples_split': 2, 'min_samples_leaf': 3, 'subsample': 0.7407326911978687}
Best GradientBoosting RMSE: 0.11861192174732638
Tuned GradientBoosting RMSE: 0.11861


In [26]:
# Optuna optimization for Bagging
def objective_br(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 50, 500),
        'max_samples': trial.suggest_float('max_samples', 0.5, 1.0),
        'max_features': trial.suggest_float('max_features', 0.5, 1.0)
    }
    bagging = BaggingRegressor(**params, random_state=42)
    bagging.fit(X_train, y_train)
    pred = bagging.predict(X_val)
    rmse = np.sqrt(mean_squared_error(y_val, pred))
    return rmse

# Optimize hyperparameters with Optuna
study_bagging = optuna.create_study(direction='minimize')
study_bagging.optimize(objective_br, n_trials=n_trials)
print("Best Bagging params:", study_bagging.best_params)
print("Best Bagging RMSE:", study_bagging.best_value)

# retrain
bagging_best = BaggingRegressor(**study_bagging.best_params, random_state=42)
bagging_best.fit(X_train, y_train)
bagging_best_pred = bagging_best.predict(X_val)
bagging_best_rmse = np.sqrt(mean_squared_error(y_val, bagging_best_pred))
print(f"Tuned Bagging RMSE: {bagging_best_rmse:.5f}")

[I 2025-08-17 19:08:54,486] A new study created in memory with name: no-name-1a49b2c8-29f8-44b9-bbbf-ea9577a583a1
[I 2025-08-17 19:08:55,773] Trial 0 finished with value: 0.14573467939342635 and parameters: {'n_estimators': 60, 'max_samples': 0.9997661407545606, 'max_features': 0.7331700958027279}. Best is trial 0 with value: 0.14573467939342635.
[I 2025-08-17 19:09:00,769] Trial 1 finished with value: 0.1451526192350068 and parameters: {'n_estimators': 271, 'max_samples': 0.8535891381701377, 'max_features': 0.7380685141185868}. Best is trial 1 with value: 0.1451526192350068.
[I 2025-08-17 19:09:08,324] Trial 2 finished with value: 0.14589141465304606 and parameters: {'n_estimators': 400, 'max_samples': 0.7035398866867457, 'max_features': 0.9128540570528765}. Best is trial 1 with value: 0.1451526192350068.
[I 2025-08-17 19:09:09,608] Trial 3 finished with value: 0.14464403709513698 and parameters: {'n_estimators': 73, 'max_samples': 0.901436677395903, 'max_features': 0.7007259399996244

Best Bagging params: {'n_estimators': 220, 'max_samples': 0.7138590902061488, 'max_features': 0.5026361093709761}
Best Bagging RMSE: 0.1390399794081062
Tuned Bagging RMSE: 0.13904


In [27]:
# Optuna optimization for TabNet
def objective_tabnet(trial):
    params = {
        'n_d': trial.suggest_int('n_d', 8, 64),
        'n_a': trial.suggest_int('n_a', 8, 64),
        'n_steps': trial.suggest_int('n_steps', 3, 10),
        'gamma': trial.suggest_float('gamma', 1.0, 2.0),
        'lambda_sparse': trial.suggest_float('lambda_sparse', 0.0001, 0.1, log=True)
    }
    tabnet = TabNetRegressor(**params, seed=42)
    tabnet.fit(
        X_train.values, y_train.values.reshape(-1, 1),
        eval_set=[(X_val.values, y_val.values.reshape(-1, 1))],
        eval_metric=['rmse'],
        max_epochs=100,
        patience=10,
        batch_size=1024,
        virtual_batch_size=128
    )
    pred = tabnet.predict(X_val.values).flatten()
    rmse = np.sqrt(mean_squared_error(y_val, pred))
    return rmse

# Optimize hyperparameters with Optuna
study_tabnet = optuna.create_study(direction='minimize')
study_tabnet.optimize(objective_tabnet, n_trials=200)
print("Best TabNet params:", study_tabnet.best_params)
print("Best TabNet RMSE:", study_tabnet.best_value)

# retrain tabnet
tabnet_best = TabNetRegressor(**study_tabnet.best_params, seed=42)
tabnet_best.fit(
    X_train.values, y_train.values.reshape(-1, 1),
    eval_set=[(X_val.values, y_val.values.reshape(-1, 1))],
    eval_metric=['rmse'],
    max_epochs=100,
    patience=10,
    batch_size=1024,
    virtual_batch_size=128
)
tabnet_best_pred = tabnet_best.predict(X_val.values).flatten()
tabnet_best_rmse = np.sqrt(mean_squared_error(y_val, tabnet_best_pred))
print(f"Tuned TabNet RMSE: {tabnet_best_rmse:.5f}")

[I 2025-08-17 19:33:13,801] A new study created in memory with name: no-name-d1c1d06a-7bb7-4b46-970f-cde3b381912a
C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\pytorch_tabnet\abstract_model.py:82: UserWarning: Device used : cpu
  warnings.warn(f"Device used : {self.device}")


epoch 0  | loss: 191.57555| val_0_rmse: 18.06934|  0:00:00s
epoch 1  | loss: 137.81482| val_0_rmse: 11.0719 |  0:00:00s
epoch 2  | loss: 97.03248| val_0_rmse: 8.49918 |  0:00:00s
epoch 3  | loss: 66.91883| val_0_rmse: 7.56094 |  0:00:00s
epoch 4  | loss: 42.99661| val_0_rmse: 7.67537 |  0:00:00s
epoch 5  | loss: 32.21754| val_0_rmse: 7.20312 |  0:00:01s
epoch 6  | loss: 22.17604| val_0_rmse: 8.26113 |  0:00:01s
epoch 7  | loss: 15.96772| val_0_rmse: 9.30673 |  0:00:01s
epoch 8  | loss: 16.83532| val_0_rmse: 10.36075|  0:00:01s
epoch 9  | loss: 16.8701 | val_0_rmse: 8.8023  |  0:00:01s
epoch 10 | loss: 15.23916| val_0_rmse: 7.84967 |  0:00:01s
epoch 11 | loss: 11.68878| val_0_rmse: 6.93089 |  0:00:01s
epoch 12 | loss: 8.97382 | val_0_rmse: 5.97524 |  0:00:02s
epoch 13 | loss: 6.07834 | val_0_rmse: 5.18581 |  0:00:02s
epoch 14 | loss: 4.69125 | val_0_rmse: 4.6964  |  0:00:02s
epoch 15 | loss: 5.0841  | val_0_rmse: 4.85472 |  0:00:02s
epoch 16 | loss: 4.14344 | val_0_rmse: 5.66569 |  0:00

C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\pytorch_tabnet\callbacks.py:172: UserWarning: Best weights from best epoch are automatically used!
  warnings.warn(wrn_msg)
[I 2025-08-17 19:33:17,818] Trial 0 finished with value: 4.696403919871648 and parameters: {'n_d': 42, 'n_a': 53, 'n_steps': 5, 'gamma': 1.0051910353909734, 'lambda_sparse': 0.0029858944846183}. Best is trial 0 with value: 4.696403919871648.


epoch 24 | loss: 1.02547 | val_0_rmse: 5.26086 |  0:00:03s

Early stopping occurred at epoch 24 with best_epoch = 14 and best_val_0_rmse = 4.6964


C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\pytorch_tabnet\abstract_model.py:82: UserWarning: Device used : cpu
  warnings.warn(f"Device used : {self.device}")


...

C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\pytorch_tabnet\callbacks.py:172: UserWarning: Best weights from best epoch are automatically used!
  warnings.warn(wrn_msg)
[I 2025-08-17 19:57:07,225] Trial 199 finished with value: 6.895805911331691 and parameters: {'n_d': 25, 'n_a': 52, 'n_steps': 3, 'gamma': 1.0911139005617336, 'lambda_sparse': 0.0022011322558988856}. Best is trial 163 with value: 0.19407104242042633.


epoch 17 | loss: 4.76156 | val_0_rmse: 17.30763|  0:00:01s
epoch 18 | loss: 4.30708 | val_0_rmse: 13.26   |  0:00:01s

Early stopping occurred at epoch 18 with best_epoch = 8 and best_val_0_rmse = 6.89581
Best TabNet params: {'n_d': 39, 'n_a': 57, 'n_steps': 3, 'gamma': 1.521073730613384, 'lambda_sparse': 0.007316938863543923}
Best TabNet RMSE: 0.19407104242042633


C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\pytorch_tabnet\abstract_model.py:82: UserWarning: Device used : cpu
  warnings.warn(f"Device used : {self.device}")


epoch 0  | loss: 207.52904| val_0_rmse: 16.709  |  0:00:00s
epoch 1  | loss: 163.26042| val_0_rmse: 12.5529 |  0:00:00s
epoch 2  | loss: 131.57022| val_0_rmse: 10.7921 |  0:00:00s
epoch 3  | loss: 107.45393| val_0_rmse: 9.58088 |  0:00:00s
epoch 4  | loss: 86.54867| val_0_rmse: 8.95766 |  0:00:00s
epoch 5  | loss: 68.47581| val_0_rmse: 8.35169 |  0:00:00s
epoch 6  | loss: 53.32837| val_0_rmse: 7.73243 |  0:00:00s
epoch 7  | loss: 37.12438| val_0_rmse: 7.2653  |  0:00:00s
epoch 8  | loss: 25.71351| val_0_rmse: 6.36269 |  0:00:00s
epoch 9  | loss: 15.74526| val_0_rmse: 6.57215 |  0:00:01s
epoch 10 | loss: 9.25364 | val_0_rmse: 9.78087 |  0:00:01s
epoch 11 | loss: 5.42163 | val_0_rmse: 10.73247|  0:00:01s
epoch 12 | loss: 4.87476 | val_0_rmse: 8.46662 |  0:00:01s
epoch 13 | loss: 4.75264 | val_0_rmse: 7.00895 |  0:00:01s
epoch 14 | loss: 4.43995 | val_0_rmse: 6.75142 |  0:00:01s
epoch 15 | loss: 3.13917 | val_0_rmse: 6.30315 |  0:00:01s
epoch 16 | loss: 1.93881 | val_0_rmse: 6.47245 |  0:

C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\pytorch_tabnet\callbacks.py:172: UserWarning: Best weights from best epoch are automatically used!
  warnings.warn(wrn_msg)


In [28]:
# Optuna optimization for bayesian ridge
def objective_br(trial):
    params = {
        'alpha_1': trial.suggest_float('alpha_1', 1e-6, 1e-1, log=True),
        'alpha_2': trial.suggest_float('alpha_2', 1e-6, 1e-1, log=True),
        'lambda_1': trial.suggest_float('lambda_1', 1e-6, 1e-1, log=True),
        'lambda_2': trial.suggest_float('lambda_2', 1e-6, 1e-1, log=True)
    }
    bayesian_ridge = BayesianRidge(**params)
    bayesian_ridge.fit(X_train, y_train)
    pred = bayesian_ridge.predict(X_val)
    rmse = np.sqrt(mean_squared_error(y_val, pred))
    return rmse

# Optimize hyperparameters with Optuna
study_bayesian = optuna.create_study(direction='minimize')
study_bayesian.optimize(objective_br, n_trials=n_trials)
print("Best Bayesian params:", study_bayesian.best_params)
print("Best Bayesian RMSE:", study_bayesian.best_value)

# retrain
bayesian_best = BayesianRidge(**study_bayesian.best_params)
bayesian_best.fit(X_train, y_train)
bayesian_best_pred = bayesian_best.predict(X_val)
bayesian_best_rmse = np.sqrt(mean_squared_error(y_val, bayesian_best_pred))
print(f"Tuned Bayesian RMSE: {bayesian_best_rmse:.5f}")


[I 2025-08-17 19:57:17,647] A new study created in memory with name: no-name-2d50bf2f-425c-4cb6-a9d7-da74cd35b421
[I 2025-08-17 19:57:17,689] Trial 0 finished with value: 0.12834342437766919 and parameters: {'alpha_1': 0.00026192608138955845, 'alpha_2': 1.7238918348084623e-05, 'lambda_1': 0.025189689292711537, 'lambda_2': 5.690395952339314e-06}. Best is trial 0 with value: 0.12834342437766919.
[I 2025-08-17 19:57:17,724] Trial 1 finished with value: 0.128241709267092 and parameters: {'alpha_1': 2.329405388708585e-06, 'alpha_2': 7.994269953359608e-05, 'lambda_1': 0.00017847819814141843, 'lambda_2': 0.0026189459917066536}. Best is trial 1 with value: 0.128241709267092.
[I 2025-08-17 19:57:17,757] Trial 2 finished with value: 0.12784040321873866 and parameters: {'alpha_1': 0.00589770665936801, 'alpha_2': 0.00022271263425587587, 'lambda_1': 6.875217385976214e-05, 'lambda_2': 0.019178606453372053}. Best is trial 2 with value: 0.12784040321873866.
[I 2025-08-17 19:57:17,789] Trial 3 finished

Best Bayesian params: {'alpha_1': 0.012731171520308912, 'alpha_2': 2.9285944006861126e-06, 'lambda_1': 0.00045803986639731417, 'lambda_2': 0.09998551159924475}
Best Bayesian RMSE: 0.12711416431961847
Tuned Bayesian RMSE: 0.12711


In [ ]:
print(f"1,best RF rmse:{rf_best_rmse}")
print(f"2,best XGBoost rmse:{xgb_best_rmse}")
print(f"3,best LightGBM rmse:{lgb_best_rmse}")
print(f"4,best CatBoost rmse:{catboost_best_rmse}")
print(f"5,best ElasticNet rmse:{enet_best_rmse}")
print(f"6,best Huber rmse:{huber_best_rmse}")
print(f"7,best MLP rmse:{mlp_best_rmse}")
print(f"8,best kernelRidge rmse: {kr_best_rmse}")
print(f"9,best SVR rmse:{svr_best_rmse}")
print(f"10,best ridge rmse:{ridge_best_rmse}")
print(f"11,best lasso rmse:{lasso_best_rmse}")
print(f"12,best gbr rmse: {gbr_best_rmse}")
print(f"13,best bagging rmse: {bagging_best_rmse}")
print(f"15,best bayesian rmse: {bayesian_best_rmse}")
print(f"14,best tabnet rmse: {tabnet_best_rmse}")



1,best RF rmse:0.14611456417269725
2,best XGBoost rmse:0.11912768981539701
3,best LightGBM rmse:0.1243647991046035
4,best CatBoost rmse:0.11282777979590002
5,best ElasticNet rmse:0.12616595750639695
6,best Huber rmse:0.12390182950494899
7,best MLP rmse:0.15270290898143354
8,best kernelRidge rmse: 0.12293212209914134
9,best SVR rmse:0.1189349723278028
10,best ridge rmse:0.1261635855204583
11,best lasso rmse:0.12638472958333277
12,best gbr rmse: 0.11861192174732638
13,best bagging rmse: 0.1390399794081062
15,best bayesian rmse: 0.12711416431961847
14,best tabnet rmse: 0.19407104242042633


In [30]:
# # feature importance visualization
# # Random Forest feature importance
# rf_importance = pd.Series(rf_best.feature_importances_, index=X.columns).sort_values(ascending=False)
# plt.figure(figsize=(10, 6))
# rf_importance[:30].plot(kind='bar')
# plt.title('Random Forest top 10 feature importance')
# plt.show()

# # # XGBoost feature importance
# # xgb_importance = pd.Series(xgb_best.feature_importances_, index=X.columns).sort_values(ascending=False)
# # plt.figure(figsize=(10, 6))
# # xgb_importance[:30].plot(kind='bar')
# # plt.title('XGBoost top 10 feature importance')
# # plt.show()

# # LightGBM feature importance
# lgb_importance = pd.Series(lgb_best.feature_importances_, index=X.columns).sort_values(ascending=False)
# plt.figure(figsize=(10, 6))
# lgb_importance[:30].plot(kind='bar')
# plt.title('LightGBM top 10 feature importance')
# plt.show()

# # CatBoost feature importance
# catboost_importance = pd.Series(catboost_best.feature_importances_, index=X.columns).sort_values(ascending=False)
# plt.figure(figsize=(10, 6))
# catboost_importance[:30].plot(kind='bar')
# plt.title('CatBoost top 10 feature importance')
# plt.show()

# # ElasticNet feature importance
# enet_importance = pd.Series(np.abs(enet_best.coef_), index=X.columns).sort_values(ascending=False)
# plt.figure(figsize=(10, 6))
# enet_importance[:30].plot(kind='bar')
# plt.title('ElasticNet top 10 feature importance')
# plt.show()

# # Huber feature importance
# huber_importance = pd.Series(np.abs(huber_best.coef_), index=X.columns).sort_values(ascending=False)
# plt.figure(figsize=(10, 6))
# huber_importance[:30].plot(kind='bar')
# plt.title('Huber top 10 feature importance')
# plt.show()

# # MLP feature importance
# perm_importance = permutation_importance(mlp_best, X_val, y_val, n_repeats=10, random_state=42)
# mlp_importance = pd.Series(perm_importance.importances_mean, index=X.columns).sort_values(ascending=False)
# plt.figure(figsize=(10, 6))
# mlp_importance[:30].plot(kind='bar')
# plt.title('MLP top 10 feature importance')
# plt.show()

# # KernelRidge feature importance, no feature importance available

# # SVR feature importance, no feature importance available

# # # Feature importance for GradientBoosting
# # gbr_importance = pd.Series(gbr_best.feature_importances_, index=X.columns).sort_values(ascending=False)
# # plt.figure(figsize=(10, 6))
# # gbr_importance[:10].plot(kind='bar')
# # plt.title('GradientBoosting Top 10 Feature Importance')
# # plt.show()


In [31]:
# # Random Forest cross-validation
# rf_cv_scores = cross_val_score(rf_best, X, y, cv=5, scoring='neg_root_mean_squared_error')
# print(f"Random Forest cross-validation RMSE: {-rf_cv_scores.mean():.5f} (+/- {rf_cv_scores.std() * 2:.5f})")

# # # XGBoost cross-validation
# # xgb_cv_scores = cross_val_score(xgb_best, X, y, cv=5, scoring='neg_root_mean_squared_error')
# # print(f"XGBoost cross-validation RMSE: {-xgb_cv_scores.mean():.5f} (+/- {xgb_cv_scores.std() * 2:.5f})")

# # LightGBM cross-validation
# lgb_cv_scores = cross_val_score(lgb_best, X, y, cv=5, scoring='neg_root_mean_squared_error')
# print(f"LightGBM cross-validation RMSE: {-lgb_cv_scores.mean():.5f} (+/- {lgb_cv_scores.std() * 2:.5f})")

# # CatBoost cross-validation
# catboost_cv_scores = cross_val_score(catboost_best, X, y, cv=5, scoring='neg_root_mean_squared_error')
# print(f"CatBoost cross-validation RMSE: {-catboost_cv_scores.mean():.5f} (+/- {catboost_cv_scores.std() * 2:.5f})")

# # ElasticNet cross-validation
# enet_cv_scores = cross_val_score(enet_best, X, y, cv=5, scoring='neg_root_mean_squared_error')
# print(f"ElasticNet cross-validation RMSE: {-enet_cv_scores.mean():.5f} (+/- {enet_cv_scores.std() * 2:.5f})")

# # Huber cross-validation
# huber_cv_scores = cross_val_score(huber_best, X, y, cv=5, scoring='neg_root_mean_squared_error')
# print(f"Huber cross-validation RMSE: {-huber_cv_scores.mean():.5f} (+/- {huber_cv_scores.std() * 2:.5f})")

# # MLP cross-validation
# mlp_cv_scores = cross_val_score(mlp_best, X, y, cv=5, scoring='neg_root_mean_squared_error')
# print(f"MLP cross-validation RMSE: {-mlp_cv_scores.mean():.5f} (+/- {mlp_cv_scores.std() * 2:.5f})")

# # # KernelRidge cross-validation
# # kr_cv_scores = cross_val_score(kr_best, X, y, cv=5, scoring='neg_root_mean_squared_error')
# # print(f"KernelRidge cross-validation RMSE: {-kr_cv_scores.mean():.5f} (+/- {kr_cv_scores.std() * 2:.5f})")

# # # SVR cross-validation
# # svr_cv_scores = cross_val_score(svr_best, X, y, cv=5, scoring='neg_root_mean_squared_error')
# # print(f"SVR cross-validation RMSE: {-svr_cv_scores.mean():.5f} (+/- {svr_cv_scores.std() * 2:.5f})")

# # # Cross-validation
# # ridge_cv_scores = cross_val_score(ridge_best, X, y, cv=5, scoring='neg_root_mean_squared_error')
# # print(f"Ridge CV RMSE: {-ridge_cv_scores.mean():.5f} (+/- {ridge_cv_scores.std() * 2:.5f})")

# # lasso_cv_scores = cross_val_score(lasso_best, X, y, cv=5, scoring='neg_root_mean_squared_error')
# # print(f"Lasso CV RMSE: {-lasso_cv_scores.mean():.5f} (+/- {lasso_cv_scores.std() * 2:.5f})")

# # gbr_cv_scores = cross_val_score(gbr_best, X, y, cv=5, scoring='neg_root_mean_squared_error')
# # print(f"GradientBoosting CV RMSE: {-gbr_cv_scores.mean():.5f} (+/- {gbr_cv_scores.std() * 2:.5f})")

# # br_cv_scores = cross_val_score(br_best, X, y, cv=5, scoring='neg_root_mean_squared_error')
# # print(f"Bagging CV RMSE: {-br_cv_scores.mean():.5f} (+/- {br_cv_scores.std() * 2:.5f})")


In [37]:
# predict on test set
xgb_test_pred = xgb_best.predict(X_test)
lgb_test_pred = lgb_best.predict(X_test)
catboost_test_pred = catboost_best.predict(X_test)
svr_test_pred = svr_best.predict(X_test)
gbr_test_pred = gbr_best.predict(X_test)
huber_test_pred = huber_best.predict(X_test)
kr_test_pred = kr_best.predict(X_test)
enet_test_pred = enet_best.predict(X_test)
ridge_test_pred = ridge_best.predict(X_test)
lasso_test_pred = lasso_best.predict(X_test)
bayesian_test_pred = bayesian_best.predict(X_test)

# simple ensemble (average predictions)
final_pred = (catboost_test_pred + xgb_test_pred + lgb_test_pred + 
              huber_test_pred + kr_test_pred + svr_test_pred + gbr_test_pred +
              enet_test_pred + ridge_test_pred + lasso_test_pred + bayesian_test_pred) / 11

# expm1 transformation to reverse log transformation
final_pred = np.expm1(final_pred)

# save submission file
submission = pd.DataFrame({'Id': test_ID, 'SalePrice': final_pred})
submission.to_csv('submission_baseline_6Models.csv', index=False)

In [38]:
# define base models for stacking
base_models = [
    ('xgb', XGBRegressor(**xgb_best_params, random_state=42)),
    ('lgb', LGBMRegressor(**lgb_best_params, random_state=42, verbose=-1)),
    ('catboost', CatBoostRegressor(**catboost_best_params, random_state=42, verbose=0)),
    ('svr', SVR(**svr_best_params)),
    ('gbr', GradientBoostingRegressor(**study_gbr.best_params, random_state=42)),
    ('huber', HuberRegressor(**huber_best_params)),
    ('kr', KernelRidge(**kr_best_params)),
    ('enet', ElasticNet(**enet_best_params, random_state=42)),
    ('ridge', Ridge(**study_ridge.best_params, random_state=42)),
    ('lasso', Lasso(**study_lasso.best_params, random_state=42)),
    ('bayesian', BayesianRidge(**study_bayesian.best_params))
]

# define meta learner
meta_learner = Ridge()
# first try use normal parameters for LGBMRegressor
# meta_learner = LGBMRegressor(n_estimators=100, learning_rate=0.05, max_depth=3, 
#                             num_leaves=15, random_state=42)
# initia Stacking
stacking_model = StackingRegressor(estimators=base_models, final_estimator=meta_learner, cv=5)

# train Stacking model
stacking_model.fit(X_train, y_train)

# validate Stacking model
stacking_pred = stacking_model.predict(X_val)
stacking_rmse = np.sqrt(mean_squared_error(y_val, stacking_pred))
print(f"Stacking RMSE: {stacking_rmse:.5f}")

# cross-validation
stacking_cv_scores = cross_val_score(stacking_model, X, y, cv=5, scoring='neg_root_mean_squared_error')
print(f"Stacking cross-validation RMSE: {-stacking_cv_scores.mean():.5f} (+/- {stacking_cv_scores.std() * 2:.5f})")

# predict on test set
stacking_test_pred = stacking_model.predict(X_test)
stacking_test_pred = np.expm1(stacking_test_pred)

# save submission file
print(f"Stacking RMSE: {stacking_rmse:.5f}")
submission_stacking = pd.DataFrame({'Id': test_ID, 'SalePrice': stacking_test_pred})
submission_stacking.to_csv('submission_stacking_6Models.csv', index=False)

C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\sklearn\linear_model\_huber.py:343: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. OF ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
  self.n_iter_ = _check_optimize_result("lbfgs", opt_res, self.max_iter)
C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\sklearn\linear_model\_coordinate_descent.py:695: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 4.689e+00, tolerance: 1.819e-02
  model = cd_fast.enet_coordinate_descent(
C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\sklearn\linear_model\_coordinate_descent.py:695: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, chec

Stacking RMSE: 0.11231


C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\sklearn\linear_model\_huber.py:343: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. OF ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
  self.n_iter_ = _check_optimize_result("lbfgs", opt_res, self.max_iter)
C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\sklearn\linear_model\_coordinate_descent.py:695: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 4.719e+00, tolerance: 1.846e-02
  model = cd_fast.enet_coordinate_descent(
C:\Users\Liuji\AppData\Roaming\Python\Python313\site-packages\sklearn\linear_model\_coordinate_descent.py:695: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, chec

Stacking cross-validation RMSE: 0.10975 (+/- 0.00900)
Stacking RMSE: 0.11231
